# Music Generation Using Deep Learning

In [1]:
import os
import json
import argparse
import pandas as pd
import numpy as np

from model import build_model, save_weights

In [3]:
DATA_DIR = './data'
LOG_DIR = './logs'

BATCH_SIZE = 16
SEQ_LENGTH = 64
name_of_file = 'input'

In [5]:
text = open(os.path.join('data', name_of_file+".txt") ).read()

In [39]:
text

'X: 1\nT:A and D\n% Nottingham Music Database\nS:EF\nY:AB\nM:4/4\nK:A\nM:6/8\nP:A\nf|"A"ecc c2f|"A"ecc c2f|"A"ecc c2f|"Bm"BcB "E7"B2f|\n"A"ecc c2f|"A"ecc c2c/2d/2|"D"efe "E7"dcB| [1"A"Ace a2:|\n [2"A"Ace ag=g||\nK:D\nP:B\n"D"f2f Fdd|"D"AFA f2e/2f/2|"G"g2g ecd|"Em"efd "A7"cBA|\n"D"f^ef dcd|"D"AFA f=ef|"G"gfg "A7"ABc |[1"D"d3 d2e:|[2"D"d3 d2||\n\n\nX: 2\nT:Abacus\n% Nottingham Music Database\nS:By Hugh Barwell, via Phil Rowe\nM:6/8\nK:G\n"G"g2g B^AB|d2d G3|"Em"GAB "Am"A2A|"D7"ABc "G"BAG|\n"G"g2g B^AB|d2d G2G|"Em"GAB "Am"A2G|"D7"FGA "G"G3:||:\n"D7"A^GA DFA|"G"B^AB G3|"A7"^c=c^c A^ce|"D7"fef def|\n"G"g2g de=f|"E7"e2e Bcd|"Am"c2c "D7"Adc| [1"G"B2A G3:|\n [2"G"B2A G2F||"Em"E2E G2G|B2B e2e|"Am"c2A "B7"FBA|"Em"G2F E3|"Em"EFG "Am"ABc|\n"B7"B^c^d "Em"e2e|"F#7"f2f f2e|"B7"^def BAF|"Em"E2E G2G|B2B e2e|\n"Am"c2A "B7"FBA|"Em"G2F E3|"Em"EFG "Am"ABc|"B7"B^c^d "Em"e2e|\n"F#7"f2e "B7"^def |[1"Em"e3 "D7"d3:|[2"Em"e3 "E7"e3||\n\n\nX: 3\nT:The American Dwarf\n% Nottingham Music Database\nS:FTB, via EF\nM:6

In [6]:
 # character to index and vice-versa mappings
char_to_idx = { ch: i for (i, ch) in enumerate(sorted(list(set(open(os.path.join('data', name_of_file+".txt") ).read()))))}
print("Number of unique characters: " + str(len(char_to_idx))) #86

with open(os.path.join(DATA_DIR, 'char_to_idx.json'), 'w') as f:
     json.dump(char_to_idx, f)

idx_to_char = { i: ch for (ch, i) in char_to_idx.items() }
vocab_size = len(char_to_idx)

Number of unique characters: 86


In [7]:
print(list(enumerate(sorted(list(set(open(os.path.join('data', name_of_file+".txt") ).read()))))))

[(0, '\n'), (1, ' '), (2, '!'), (3, '"'), (4, '#'), (5, '%'), (6, '&'), (7, "'"), (8, '('), (9, ')'), (10, '+'), (11, ','), (12, '-'), (13, '.'), (14, '/'), (15, '0'), (16, '1'), (17, '2'), (18, '3'), (19, '4'), (20, '5'), (21, '6'), (22, '7'), (23, '8'), (24, '9'), (25, ':'), (26, '='), (27, '?'), (28, 'A'), (29, 'B'), (30, 'C'), (31, 'D'), (32, 'E'), (33, 'F'), (34, 'G'), (35, 'H'), (36, 'I'), (37, 'J'), (38, 'K'), (39, 'L'), (40, 'M'), (41, 'N'), (42, 'O'), (43, 'P'), (44, 'Q'), (45, 'R'), (46, 'S'), (47, 'T'), (48, 'U'), (49, 'V'), (50, 'W'), (51, 'X'), (52, 'Y'), (53, '['), (54, '\\'), (55, ']'), (56, '^'), (57, '_'), (58, 'a'), (59, 'b'), (60, 'c'), (61, 'd'), (62, 'e'), (63, 'f'), (64, 'g'), (65, 'h'), (66, 'i'), (67, 'j'), (68, 'k'), (69, 'l'), (70, 'm'), (71, 'n'), (72, 'o'), (73, 'p'), (74, 'q'), (75, 'r'), (76, 's'), (77, 't'), (78, 'u'), (79, 'v'), (80, 'w'), (81, 'x'), (82, 'y'), (83, 'z'), (84, '|'), (85, '~')]


In [8]:
len(text)/16

8104.0625

In [9]:
def read_batches(T, vocab_size):
    length = T.shape[0]; #129,665
    batch_chars = int(length / BATCH_SIZE); # 8,104

    for start in range(0, batch_chars - SEQ_LENGTH, SEQ_LENGTH): # (0, 8040, 64)
        X = np.zeros((BATCH_SIZE, SEQ_LENGTH)) # 16X64
        Y = np.zeros((BATCH_SIZE, SEQ_LENGTH, vocab_size)) # 16X64X86
        for batch_idx in range(0, BATCH_SIZE): # (0,16)
            for i in range(0, SEQ_LENGTH): #(0,64)
                X[batch_idx, i] = T[batch_chars * batch_idx + start + i] # 
                Y[batch_idx, i, T[batch_chars * batch_idx + start + i + 1]] = 1
        yield X, Y

In [10]:

def train(text, epochs=100, save_freq=10):

    # character to index and vice-versa mappings
    char_to_idx = { ch: i for (i, ch) in enumerate(sorted(list(set(text)))) }
    print("Number of unique characters: " + str(len(char_to_idx))) #86

    with open(os.path.join(DATA_DIR, 'char_to_idx.json'), 'w') as f:
        json.dump(char_to_idx, f)

    idx_to_char = { i: ch for (ch, i) in char_to_idx.items() }
    vocab_size = len(char_to_idx)

    #model_architecture
    model = build_model(BATCH_SIZE, SEQ_LENGTH, vocab_size)
    model.summary()
    model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])


    #Train data generation
    T = np.asarray([char_to_idx[c] for c in text], dtype=np.int32) #convert complete text into numerical indices

    print("Length of text:" + str(T.size)) #129,665

    steps_per_epoch = (len(text) / BATCH_SIZE - 1) / SEQ_LENGTH  

    log = TrainLogger('training_log.csv')

    for epoch in range(epochs):
        print('\nEpoch {}/{}'.format(epoch + 1, epochs))
        
        losses, accs = [], []

        for i, (X, Y) in enumerate(read_batches(T, vocab_size)):
            
            print(X);

            loss, acc = model.train_on_batch(X, Y)
            print('Batch {}: loss = {}, acc = {}'.format(i + 1, loss, acc))
            losses.append(loss)
            accs.append(acc)

        log.add_entry(np.average(losses), np.average(accs))

        if (epoch + 1) % save_freq == 0:
            save_weights(epoch + 1, model)
            print('Saved checkpoint to', 'weights.{}.h5'.format(epoch + 1))

In [11]:

class TrainLogger(object):
    def __init__(self, file):
        self.file = os.path.join(LOG_DIR, file)
        self.epochs = 0
        with open(self.file, 'w') as f:
            f.write('epoch,loss,acc\n')

    def add_entry(self, loss, acc):
        self.epochs += 1
        s = '{},{},{}\n'.format(self.epochs, loss, acc)
        with open(self.file, 'a') as f:
            f.write(s)

In [8]:
vocab_size=86
import os

from keras.models import Sequential, load_model
from keras.layers import LSTM, Dropout, TimeDistributed, Dense, Activation, Embedding

In [13]:
MODEL_DIR = './model'

In [14]:
def save_weights(epoch, model):
    if not os.path.exists(MODEL_DIR):
        os.makedirs(MODEL_DIR)
    model.save_weights(os.path.join(MODEL_DIR, 'weights.{}.h5'.format(epoch)))

def load_weights(epoch, model):
    model.load_weights(os.path.join(MODEL_DIR, 'weights.{}.h5'.format(epoch)))

def build_model(batch_size, seq_len, vocab_size):
    model = Sequential()
    model.add(Embedding(vocab_size, 512, batch_input_shape=(batch_size, seq_len)))
    for i in range(3):
        model.add(LSTM(256, return_sequences=True, stateful=True))
        model.add(Dropout(0.2))

    model.add(TimeDistributed(Dense(vocab_size))) 
    model.add(Activation('softmax'))
    return model

In [15]:
train(text)

Number of unique characters: 86
Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding (Embedding)        (16, 64, 512)             44032     
_________________________________________________________________
lstm (LSTM)                  (16, 64, 256)             787456    
_________________________________________________________________
dropout (Dropout)            (16, 64, 256)             0         
_________________________________________________________________
lstm_1 (LSTM)                (16, 64, 256)             525312    
_________________________________________________________________
dropout_1 (Dropout)          (16, 64, 256)             0         
_________________________________________________________________
lstm_2 (LSTM)                (16, 64, 256)             525312    
_________________________________________________________________
dropout_2 (Dropout)     

Batch 27: loss = 3.2366671562194824, acc = 0.1884765625
[[29.  1.  3. ... 28. 84.  3.]
 [63. 84.  3. ... 18.  1.  3.]
 [ 3. 34.  3. ... 31.  3. 63.]
 ...
 [28. 33. 31. ...  3. 34. 18.]
 [61. 60. 84. ... 60. 84.  3.]
 [84.  3. 30. ... 34. 70.  3.]]
Batch 28: loss = 3.3615353107452393, acc = 0.1669921875
[[28.  3. 62. ...  3. 28.  3.]
 [34.  3. 61. ...  3. 31.  3.]
 [61. 61.  1. ... 25. 40. 66.]
 ...
 [ 1.  3. 29. ...  3. 29. 60.]
 [31.  3. 61. ...  1.  3. 28.]
 [64. 17. 34. ... 61. 60. 29.]]
Batch 29: loss = 3.7654147148132324, acc = 0.1328125
[[58. 62. 60. ... 25. 33. 72.]
 [63. 17. 64. ...  1. 46. 72.]
 [68. 62.  1. ... 28. 84.  3.]
 ...
 [28.  1.  3. ...  0.  3. 32.]
 [22.  3. 29. ... 17. 33. 84.]
 [ 1. 28. 34. ... 65. 58. 70.]]
Batch 30: loss = 3.7465758323669434, acc = 0.12890625
[[75. 70. 58. ... 17. 29. 14.]
 [ 1. 29. 69. ... 33.  0. 40.]
 [34.  3. 29. ...  3. 34.  3.]
 ...
 [70.  3. 29. ... 34. 84.  3.]
 [ 3. 34.  3. ... 28.  3. 32.]
 [ 1. 40. 78. ... 84.  3. 28.]]
Batch 31: los

Batch 62: loss = 3.106775999069214, acc = 0.1708984375
[[28. 29. 28. ... 64.  0.  5.]
 [84.  0.  3. ... 25.  0. 58.]
 [63. 84.  3. ... 61.  0.  5.]
 ...
 [47. 25. 47. ... 65. 58. 70.]
 [18. 15. 24. ... 45. 72. 80.]
 [28. 62. 84. ... 84. 62. 17.]]
Batch 63: loss = 3.3143022060394287, acc = 0.1455078125
[[ 1. 41. 72. ...  3. 61. 17.]
 [84.  3. 31. ...  1. 59. 58.]
 [ 1. 41. 72. ... 31. 33. 28.]
 ...
 [ 1. 40. 78. ... 34.  3. 64.]
 [62.  0. 40. ... 61. 60. 84.]
 [61.  1. 64. ...  3. 28. 70.]]
Batch 64: loss = 3.265355110168457, acc = 0.1435546875
[[59.  1. 59. ... 64.  1. 64.]
 [64. 84.  3. ... 66. 64.  0.]
 [84.  3. 31. ...  3. 31.  3.]
 ...
 [17. 34.  1. ... 30.  3. 32.]
 [ 0.  3. 34. ...  3. 30.  3.]
 [ 3. 62. 17. ...  0.  0. 51.]]
Batch 65: loss = 3.1414263248443604, acc = 0.1591796875
[[17. 64. 84. ... 64.  1. 59.]
 [ 5.  1. 41. ... 84. 63. 14.]
 [61. 62. 61. ...  3. 62. 60.]
 ...
 [34. 34.  1. ... 61.  1. 61.]
 [60. 61. 62. ... 17. 60.  1.]
 [25.  1. 18. ... 78. 58. 69.]]
Batch 66: 

Batch 98: loss = 3.11305570602417, acc = 0.16796875
[[ 3. 28. 33. ... 32. 84.  3.]
 [63. 62. 63. ... 61. 18.  1.]
 [84.  3. 34. ...  1. 63. 62.]
 ...
 [22.  3. 34. ... 29.  0. 84.]
 [60. 84.  3. ...  3. 29. 18.]
 [61.  1.  3. ...  3. 33. 32.]]
Batch 99: loss = 2.9868390560150146, acc = 0.1865234375
[[28. 22.  3. ... 18.  1. 12.]
 [12. 61. 17. ... 59. 58. 76.]
 [63. 84.  3. ... 30. 22.  3.]
 ...
 [63. 14. 17. ... 28. 22. 14.]
 [ 1.  3. 28. ...  0.  3. 28.]
 [32.  1.  3. ... 58. 64. 84.]]
Batch 100: loss = 3.015233278274536, acc = 0.181640625
[[34. 17. 25. ... 25. 31. 72.]
 [62.  0. 46. ... 25.  3. 31.]
 [60. 61. 60. ... 84. 34. 17.]
 ...
 [62.  3. 64. ... 64. 63.  1.]
 [ 3. 62. 60. ... 62. 84.  3.]
 [ 0.  3. 31. ... 84.  0.  0.]]
Batch 101: loss = 3.0805609226226807, acc = 0.171875
[[71.  1. 40. ... 38. 25. 31.]
 [ 3. 31. 32. ... 70.  3. 28.]
 [34.  1. 34. ... 65. 58. 70.]
 ...
 [63. 62. 61. ... 10.  3. 58.]
 [31.  3. 63. ... 84.  3. 31.]
 [ 0. 51. 25. ... 58. 76. 62.]]
Batch 102: loss 

Batch 11: loss = 2.84263277053833, acc = 0.2236328125
[[60. 84.  0. ... 29.  1. 62.]
 [34. 32. 84. ... 84.  3. 34.]
 [58. 64. 84. ...  0.  0.  0.]
 ...
 [31. 22.  3. ... 60.  1. 29.]
 [31. 22.  3. ... 70.  1. 40.]
 [12.  3. 28. ... 84.  3. 31.]]
Batch 12: loss = 2.8965587615966797, acc = 0.2294921875
[[17. 62. 84. ... 62. 17. 62.]
 [ 3. 31. 34. ... 30.  3. 64.]
 [51. 25.  1. ...  1. 38. 66.]
 ...
 [17. 60. 84. ... 18.  1. 58.]
 [78. 76. 66. ... 33.  1. 34.]
 [ 3. 33. 34. ... 84. 54.  0.]]
Batch 13: loss = 2.8801701068878174, acc = 0.220703125
[[84.  0.  3. ... 18.  0. 47.]
 [63. 62. 84. ... 28. 84.  3.]
 [75. 68. 73. ... 32. 84.  3.]
 ...
 [17. 56. 58. ... 58. 18. 84.]
 [17. 61. 84. ...  1. 12. 34.]
 [ 3. 32. 70. ... 70.  1. 40.]]
Batch 14: loss = 2.811041831970215, acc = 0.23046875
[[25. 47. 65. ...  0. 40. 25.]
 [34.  3. 29. ... 58. 76. 62.]
 [34.  3. 31. ... 29. 11. 34.]
 ...
 [ 3. 34. 22. ...  1. 40. 78.]
 [17. 25. 25. ... 64. 58. 59.]
 [78. 76. 66. ... 29.  1.  3.]]
Batch 15: loss

...

Batch 91: loss = 0.2483685463666916, acc = 0.9111328125
[[ 3. 30.  3. ... 34.  1.  3.]
 [30.  3. 60. ...  3. 61. 62.]
 [ 1. 42.  7. ... 80. 62.  0.]
 ...
 [54.  0.  3. ...  0. 46. 25.]
 [66. 60.  1. ... 32. 84.  3.]
 [18.  1. 12. ...  0. 46. 25.]]
Batch 92: loss = 0.2353515625, acc = 0.927734375
[[29. 70.  3. ... 34.  3. 29.]
 [56. 64. 84. ... 77. 77. 66.]
 [40. 25. 21. ...  3. 60. 17.]
 ...
 [33. 47. 29. ... 31.  3. 61.]
 [31.  3. 33. ... 84.  0.  3.]
 [50. 72. 69. ...  1. 63. 62.]]
Batch 93: loss = 0.24351772665977478, acc = 0.916015625
[[28. 34. 84. ...  5.  1. 41.]
 [71. 64. 65. ... 25. 28.  0.]
 [25. 84.  0. ... 58. 17. 63.]
 ...
 [62. 61.  1. ... 61. 29. 28.]
 [32. 70.  3. ... 63. 17. 58.]
 [61. 84.  0. ... 84. 63. 62.]]
Batch 94: loss = 0.22320587933063507, acc = 0.91796875
[[72. 77. 77. ...  3. 34. 17.]
 [28. 84.  3. ...  1. 61. 17.]
 [ 1.  3. 30. ... 71.  1. 43.]
 ...
 [84.  3. 31. ... 28. 22.  3.]
 [ 1. 58. 63. ... 63. 84.  0.]
 [61.  1. 56. ... 61. 63.  1.]]
Batch 95: loss =

Batch 5: loss = 0.21730557084083557, acc = 0.9326171875
[[61. 18.  1. ...  1. 29. 58.]
 [64. 76. 11. ... 28. 22.  3.]
 [84.  3. 30. ...  3. 30.  3.]
 ...
 [32.  1.  3. ... 28. 29. 60.]
 [29. 70.  3. ... 17. 62. 84.]
 [34.  1.  3. ... 70.  3. 62.]]
Batch 6: loss = 0.23839494585990906, acc = 0.916015625
[[75. 80. 62. ...  3. 28. 17.]
 [62. 17. 60. ... 29. 60. 84.]
 [62. 17. 61. ... 62.  1. 35.]
 ...
 [84.  3. 32. ... 28. 70.  3.]
 [ 3. 31.  3. ... 58. 77. 58.]
 [60. 28. 84. ... 31. 17. 29.]]
Batch 7: loss = 0.22086453437805176, acc = 0.923828125
[[28. 84.  3. ...  1.  3. 34.]
 [ 3. 31.  3. ... 29. 60. 84.]
 [78. 71. 77. ... 25. 21. 14.]
 ...
 [28. 18.  1. ... 77. 77. 66.]
 [59. 58. 76. ... 29.  1. 28.]
 [ 1. 60. 17. ...  3. 28. 60.]]
Batch 8: loss = 0.2633191645145416, acc = 0.9111328125
[[ 3. 34. 18. ...  3. 34.  3.]
 [ 3. 31.  3. ...  1. 61. 17.]
 [23.  0. 38. ... 32. 70.  3.]
 ...
 [71. 64. 65. ... 30.  3. 58.]
 [34. 33. 84. ... 17. 25. 84.]
 [62.  1. 61. ...  1. 40. 78.]]
Batch 9: lo

Batch 44: loss = 0.2518857419490814, acc = 0.9228515625
[[84.  0.  3. ... 84.  3. 31.]
 [ 5.  1. 41. ...  0. 38. 25.]
 [23.  0. 38. ...  3. 28. 33.]
 ...
 [12. 28. 17. ... 32.  3. 29.]
 [22.  3. 34. ... 71. 64. 65.]
 [ 3. 60. 28. ... 33. 34. 84.]]
Batch 45: loss = 0.22718477249145508, acc = 0.91796875
[[ 3. 31. 18. ... 59. 58. 76.]
 [28. 70.  0. ... 33.  3. 60.]
 [31. 84.  0. ...  3. 31.  3.]
 ...
 [18.  1. 12. ...  1. 64. 63.]
 [58. 70.  1. ... 84.  3. 32.]
 [ 0.  3. 28. ... 25. 50. 65.]]
Batch 46: loss = 0.22177603840827942, acc = 0.9208984375
[[62.  0. 52. ...  3. 62. 18.]
 [29. 28.  1. ...  3. 30.  3.]
 [63. 58. 61. ... 22.  3. 62.]
 ...
 [62. 84.  0. ... 84.  0.  0.]
 [70.  3. 34. ...  3. 61. 56.]
 [62. 71.  1. ... 66. 71.  1.]]
Batch 47: loss = 0.2058284431695938, acc = 0.9296875
[[ 1. 62. 60. ... 28.  1.  3.]
 [60. 61. 62. ... 61. 60. 84.]
 [63. 64. 84. ... 41. 72. 77.]
 ...
 [ 0. 51. 25. ... 75. 66. 64.]
 [60. 61.  1. ... 60. 61.  1.]
 [29. 75. 66. ... 29. 60.  1.]]
Batch 48: l

Batch 83: loss = 0.2463114857673645, acc = 0.919921875
[[65. 58. 70. ... 28. 17. 28.]
 [26. 62. 63. ... 33.  1.  3.]
 [ 1. 61. 62. ...  1.  3. 28.]
 ...
 [17. 61.  1. ... 28. 17. 63.]
 [28.  1.  3. ... 64.  1. 58.]
 [28. 34.  1. ... 17. 62. 84.]]
Batch 84: loss = 0.2444484382867813, acc = 0.9189453125
[[84.  3. 34. ... 29. 34. 84.]
 [30. 70.  3. ... 31. 12. 33.]
 [22.  3. 33. ... 84.  3. 31.]
 ...
 [84.  3. 32. ... 84.  3. 31.]
 [17. 62. 84. ...  1. 63. 62.]
 [ 3. 34.  3. ...  1. 28.  1.]]
Batch 85: loss = 0.24954944849014282, acc = 0.9140625
[[54.  0.  3. ... 17. 62. 84.]
 [28.  1. 29. ... 64. 84. 63.]
 [ 3. 28. 61. ... 40. 78. 76.]
 ...
 [ 3. 61. 18. ... 76. 62.  0.]
 [62. 84.  3. ... 66. 71. 64.]
 [50. 58. 71. ... 66. 77. 66.]]
Batch 86: loss = 0.229875385761261, acc = 0.921875
[[ 3. 34.  3. ... 18. 84. 84.]
 [26. 62. 63. ...  1. 12. 63.]
 [66. 60.  1. ... 18. 28. 14.]
 ...
 [46. 25. 37. ... 62. 63. 64.]
 [65. 58. 70. ... 28. 84.  3.]
 [72. 71. 11. ... 60. 34. 32.]]
Batch 87: loss =

Batch 123: loss = 0.2559514343738556, acc = 0.91015625
[[18. 84.  3. ...  3. 29. 61.]
 [ 0.  3. 32. ...  1. 62. 18.]
 [84.  3. 31. ... 29. 84.  3.]
 ...
 [ 1. 12. 28. ... 33.  1. 28.]
 [62. 61. 60. ... 78. 75. 71.]
 [62. 17. 61. ... 18.  1. 61.]]
Batch 124: loss = 0.21737009286880493, acc = 0.9326171875
[[64.  1. 29. ... 61. 29.  1.]
 [84. 84.  0. ...  3. 61. 18.]
 [33.  3. 28. ... 61. 29. 34.]
 ...
 [60. 62. 84. ...  1. 36. 76.]
 [73. 66. 68. ... 25. 21. 14.]
 [17. 62. 84. ... 84.  3. 28.]]
Batch 125: loss = 0.22875696420669556, acc = 0.919921875
[[34. 29. 61. ... 62. 34. 29.]
 [ 1.  3. 31. ... 72. 80. 71.]
 [84.  3. 34. ... 26. 33. 18.]
 ...
 [69. 58. 71. ... 66. 58.  1.]
 [23.  0. 38. ... 60. 29. 60.]
 [ 3. 28. 29. ... 32. 70.  3.]]
Batch 126: loss = 0.24591277539730072, acc = 0.9189453125
Saved checkpoint to weights.100.h5


# Generating Music

In [9]:
def make_model(unique_chars):
    model = Sequential()
    
    model.add(Embedding(input_dim = unique_chars, output_dim = 512, batch_input_shape = (1, 1))) 
  
    model.add(LSTM(256, return_sequences = True, stateful = True))
    model.add(Dropout(0.2))
    
    model.add(LSTM(256, return_sequences = True, stateful = True))
    model.add(Dropout(0.2))
    
    model.add(LSTM(256, stateful = True)) 
    #remember, that here we haven't given return_sequences = True because here we will give only one character to generate the
    #sequence. In the end, we just have to get one output which is equivalent to getting output at the last time-stamp. So, here
    #in last layer there is no need of giving return sequences = True.
    model.add(Dropout(0.2))
    
    model.add((Dense(unique_chars)))
    model.add(Activation("softmax"))
    
    return model

In [10]:
model_weights_directory = 'model/'

In [11]:
def generate_sequence(epoch_num, initial_index, seq_length):
    with open(os.path.join(DATA_DIR, 'char_to_idx.json')) as f:
        char_to_index = json.load(f)
    index_to_char = {i:ch for ch, i in char_to_index.items()}
    unique_chars = len(index_to_char)
    
    model = make_model(unique_chars)
    model.load_weights(model_weights_directory + "weights.{}.h5".format(epoch_num))
     
    sequence_index = [initial_index]
    
    for _ in range(seq_length):
        batch = np.zeros((1, 1))
        batch[0, 0] = sequence_index[-1]
        
        predicted_probs = model.predict_on_batch(batch).ravel()
        sample = np.random.choice(range(unique_chars), size = 1, p = predicted_probs)
        
        sequence_index.append(sample[0])
    
    seq = ''.join(index_to_char[c] for c in sequence_index)
    
    cnt = 0
    for i in seq:
        cnt += 1
        if i == "\n":
            break
        seq1 = seq[cnt:]
    #above code is for ignoring the starting string of a generated sequence. This is because we are passing any arbitrary 
    #character to the model for generating music. Now, the model start generating sequence from that character itself which we 
    #have passed, so first few characters before "\n" contains meaningless word. Model start generating the music rhythm from
    #next line onwards. The correct sequence it start generating from next line onwards which we are considering.
    
    cnt = 0
    for i in seq1:
        cnt += 1
        if i == "\n" and seq1[cnt] == "\n":
            break
    seq2 = seq1[:cnt]
    #Now our data contains three newline characters after every tune. So, the model has leart that too. So, above code is used for
    #ignoring all the characters that model has generated after three new line characters. So, here we are considering only one
    #tune of music at a time and finally we are returning it..
    
    return seq2


In [13]:
ep = int(input("1. Enter the epoch number of the model you want to load. Small number will generate more errors in music: "))
ar = int(input("\n2. Enter any number between 0 to 86 which will be given as initial charcter to model for generating sequence: "))
ln = int(input("\n3. Enter the length of music sequence you want to generate. Typical number is between 300-600. Too small number will generate hardly generate any sequence: "))

music = generate_sequence(ep, ar, ln)

print("\nMUSIC SEQUENCE GENERATED: \n")

print(music)

1. Enter the epoch number of the model you want to load. Small number will generate more errors in music: 100

2. Enter any number between 0 to 86 which will be given as initial charcter to model for generating sequence: 83

3. Enter the length of music sequence you want to generate. Typical number is between 300-600. Too small number will generate hardly generate any sequence: 600

MUSIC SEQUENCE GENERATED: 


% Nottingham Music Database
S:Trad, arr Phil Rowe
M:6/8
K:D
"D"fdd "A"cAA|"G"BGG "A7"A2G|"D"FAA def|"A7"gfe "G"d3::
"D"FAA dAA|"D"FAA ffe|"G"dcB "D/f+"AFD|"Em"F3 -G2:|



In [ ]:
MUSIC SEQUENCE GENERATED: 


% Nottingham Music Database
Y:AABBCC
S:Kevin Briggs, via EF
M:4/4
K:G
M:6/8
P:A
d/2c/2|"G"BAB "Em"ede|"F"cAA A2G|"F"FAA "C"GEG|"Am"GAB "D7"DGF|"G"G3 G2:|
P:B
d|"D7"def "G"gdB|"C"cde "G"dBG|"D7"AGA A2B|"D7"cAF "G"G2:|

​